In [2]:
import os
import sys
sys.path.append('/home/wayve/prajwal/pixtrack/')
import cv2
import pycolmap
from hloc.utils import viz_3d
import numpy as np
import pixtrack.utils.pose_utils as pose_utils
from pixloc.utils.colmap import Camera as ColCamera
from pixloc.pixlib.geometry import Camera as PixCamera, Pose
import matplotlib.pyplot as plt

In [5]:
sfm_path = '/home/wayve/prajwal/pixtrack/data/pixtrack/objects/pickle_rick/pixtrack/aug_nerf_sfm/aug_sfm/'
model = pycolmap.Reconstruction(sfm_path)
#sfm_path2 = '/data/pixtrack/objects/003_cracker_box/pixtrack/pixsfm/outputs/ref/'
#model2 = pycolmap.Reconstruction(sfm_path2)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="low_res", cameras=True, cs=.5)
#viz_3d.plot_reconstruction(fig, model2, color='rgba(255,0,0,0.5)', name="high_res", cameras=True, cs=.05)
fig.show()

In [ ]:
xyzs = np.array([p3D.xyz for _, p3D in model2.points3D.items()])

In [ ]:
sfm_path = '/data/pixtrack/objects/006_mustard_bottle/pixtrack/pixsfm/outputs/ref/'
model = pycolmap.Reconstruction(sfm_path)
#sfm_path2 = '/data/pixtrack/objects/003_cracker_box/pixtrack/pixsfm/outputs/ref/'
#model2 = pycolmap.Reconstruction(sfm_path2)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="low_res", cameras=True, cs=.05)
#viz_3d.plot_reconstruction(fig, model2, color='rgba(255,0,0,0.5)', name="high_res", cameras=True, cs=.05)
fig.show()

In [ ]:
import os
os.environ['OBJ_AABB'] = "[[0., 0., 0.], [1., 1., 1.]]"
from pixtrack.utils.ingp_utils import load_nerf2sfm, sfm_to_nerf_pose

In [ ]:
def get_nerf_aabb_from_sfm(sfm_path, nerf2sfm_path):
    nerf2sfm = load_nerf2sfm(nerf2sfm_path)
    model = pycolmap.Reconstruction(sfm_path)
    points3d_in_nerf = []
    for point in model.points3D:
        pose_placeholder = np.eye(4)
        pose_placeholder[:3, -1] = model.points3D[point].xyz
        pose_placeholder_nerf = sfm_to_nerf_pose(nerf2sfm=nerf2sfm, sfm_pose=pose_placeholder)[:3, -1]
        points3d_in_nerf.append(pose_placeholder_nerf)
    points3d_in_nerf = np.array(points3d_in_nerf)
    min_xyz = points3d_in_nerf.min(axis=0)
    max_xyz = points3d_in_nerf.max(axis=0)
    min_bounds = min_xyz / 3. + np.array([0.5, 0.5, 0.5])
    max_bounds = max_xyz / 3. + np.array([0.5, 0.5, 0.5])
    aabb_bounds = [min_bounds.tolist(), max_bounds.tolist()]
    return aabb_bounds, points3d_in_nerf


In [ ]:
sfm_path = '/data/pixtrack/objects/006_mustard_bottle/pixtrack/pixsfm/outputs/ref/'
nerf2sfm_path = '/data/pixtrack/objects/006_mustard_bottle/pixtrack/pixsfm/dataset/nerf2sfm.pkl'

In [ ]:
nerf2sfm = load_nerf2sfm(nerf2sfm_path)

In [ ]:
aabb, points3d_in_nerf = get_nerf_aabb_from_sfm(sfm_path, nerf2sfm_path)

In [ ]:
np.min(points3d_in_nerf, axis=0) / 3.

In [ ]:
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(xyzs)
o3d.io.write_point_cloud("cracker_box.ply", pcd)

In [ ]:
sfm_path = '/data/pixtrack/objects/003_cracker_box/old_pixtrack/nerf_sfm/sfm/'
model = pycolmap.Reconstruction(sfm_path)
sfm_path2 = '/data/pixtrack/objects/003_cracker_box/pixtrack/nerf_sfm/sfm/'
model2 = pycolmap.Reconstruction(sfm_path2)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="low_res", cameras=True, cs=.5)
viz_3d.plot_reconstruction(fig, model2, color='rgba(255,0,0,0.5)', name="high_res", cameras=True, cs=.05)
fig.show()

In [ ]:
sfm_path = '/data/pixtrack/outputs/nerf_sfm/aug_003_cracker_box/sfm/'
model = pycolmap.Reconstruction(sfm_path)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="reference", cameras=True, cs=0.125/4)
fig.show()

In [ ]:
{model.images[x] for x in model.images if '96' in model.images[x].name}

In [ ]:
sfm_path = '/data/pixtrack/outputs/nerf_sfm/aug_003_cracker_box/aug_sfm/'
model = pycolmap.Reconstruction(sfm_path)
fig = viz_3d.init_figure()
viz_3d.plot_reconstruction(fig, model, color='rgba(0,255,0,0.5)', name="reference", cameras=True, cs=0.125/4)
fig.show()

In [ ]:
from pixtrack.utils.ingp_utils import load_nerf2sfm, initialize_ingp, sfm_to_nerf_pose
from pixtrack.visualization.run_vis_on_poses import get_nerf_image
nerf_path = '/home/prajwal.chidananda/code/pixtrack/instant-ngp/snapshots/gimble_04MAR2022/weights.msgpack'
nerf2sfm_path = '/home/prajwal.chidananda/code/pixtrack/instant-ngp/data/nerf/gimble_04MAR2022/nerf2sfm.pkl'
nerf2sfm = load_nerf2sfm(nerf2sfm_path)
testbed = initialize_ingp(nerf_path)

In [ ]:
camera = model.cameras[1]
camera = ColCamera(None, 
                camera.model_name,
                int(camera.width),
                int(camera.height),
                camera.params)
camera = PixCamera.from_colmap(camera)

In [ ]:
image = model.images[165]
cIw = pose_utils.get_camera_in_world_from_colmap_image(image)
nerf_pose = sfm_to_nerf_pose(nerf2sfm, cIw)
nerf_img = get_nerf_image(testbed, nerf_pose, camera)
plt.imshow(nerf_img)

In [ ]:
path = os.path.join('../outputs/nerf_sfm/aug_gimble_04MAR2022/', image.name)
img = cv2.imread(path, -1)
plt.imshow(img)